In [7]:
import pystac_client
from odc import stac as odc_stac
from dask.typing import Key

eodc_catalog = pystac_client.Client.open("https://stac.eodc.eu/api/v1/")
#from pystac_client import Client

#catalog = Client.open()
#print(catalog)


In [8]:
time_range = "2022-10-11/2022-10-25"
minlon, maxlon = 12.3, 13.1
minlat, maxlat = 54.3, 54.6
bounding_box = [minlon, minlat, maxlon, maxlat]
search = eodc_catalog.search(collections="GFM", bbox=bounding_box, datetime= time_range)
items_GFM = search.item_collection()
items_GFM

In [9]:
crs = "EPSG:4326"  # Coordinate Reference System - World Geodetic System 1984 (WGS84) in this case
res = 0.00018  
chunks = {"time": 1, "latitude": 1300, "longitude": 1300}
GFM_dc = odc_stac.load(items_GFM, crs=crs, chunks=chunks, resolution= res, bbox=bounding_box)


In [10]:
#from dask.distributed import wait

In [11]:
GFM_dc = GFM_dc.persist()
#wait(GFM_dc)
GFM_dc

<xarray.Dataset> Size: 4GB
Dimensions:                (latitude: 1668, longitude: 4445, time: 44)
Coordinates:
  * latitude               (latitude) float64 13kB 54.6 54.6 54.6 ... 54.3 54.3
  * longitude              (longitude) float64 36kB 12.3 12.3 12.3 ... 13.1 13.1
    spatial_ref            int32 4B 4326
  * time                   (time) datetime64[ns] 352B 2022-10-11T05:25:01 ......
Data variables:
    advisory_flags         (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    dlr_likelihood         (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    exclusion_mask         (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    tuw_likelihood         (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    list_likelihood        (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    dlr_flood_extent       (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    tuw_flood_extent       (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    list_flood_extent      (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    ensemble_likelihood    (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    reference_water_mask   (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    ensemble_flood_extent  (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    ensemble_water_extent  (time, latitude, longitude) uint8 326MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>

In [ ]:
from bokeh.models import FixedTicker
import hvplot.xarray

colorbar_opts = {
    "major_label_overrides": {
        0: "non-flood",
        1: "flood",
    },
    "ticker": FixedTicker(ticks=[0, 1]),
}

GFM_dc.hvplot.quadmesh(   x="longitude",
    y="latitude",
    rasterize=True,
    geo=True,
    cmap=["rgba(0, 0, 1, 0.1)", "darkred"],
    ).opts(frame_height=400, colorbar_opts={**colorbar_opts})

In [ ]:
from bokeh.plotting import output_notebook
output_notebook()


Loading BokehJS ...